In [2]:
import pandas as pd 
df = pd.read_csv('cleaned_generic_df_main.csv')

In [4]:
len(df['side_effects_description'].unique())

1541

In [5]:
list_of_side_effects = df['side_effects_description'].unique()

In [10]:
len(list_of_side_effects[1])

242

In [3]:
df

generic_name  \
0                     adalimumab   
1     acyclovir + hydrocortisone   
2            acyclovir (topical)   
3               acyclovir (oral)   
4         acyclovir (ophthalmic)   
...                          ...   
1706                  zinc oxide   
1707                zinc orotate   
1708                  zidovudine   
1709                    zaleplon   
1710                 zafirlukast   

                                             drug_class  \
0                                     immunosuppressant   
1                hydrocortisone & combined preparations   
2                        topical antiviral preparations   
3     herpes simplex & varicella-zoster virus infect...   
4                        ophthalmic anti-viral products   
...                                                 ...   
1706                          drugs used in diaper rash   
1707                      specific mineral preparations   
1708              drugs for hiv / anti-retroviral drugs   
1709                           benzodiazepine hypnotics   
1710                   leukotriene receptor antagonists   

                           indication  \
0                  ulcerative colitis   
1                     herpes labialis   
2                           sore lips   
3       varicella zoster (chickenpox)   
4             neonatal conjunctivitis   
...                               ...   
1706                   pressure sores   
1707                  severe diarrhea   
1708                    hiv infection   
1709  insomnia and sleep disturbances   
1710                   chronic asthma   

                                 indication_description  \
0        adalimumab is a tumor necrosis factor (tnf)...   
1      acyclovir &amp; hydrocortisone cream is indic...   
2      acyclovircream is a herpes simplex virus (hsv...   
3      aciclovir is indicated for- \r\n \r\n the tre...   
4      acyclovir is indicated for the treatment of h...   
...                                                 ...   
1706   zinc oxide helps treat and prevent diaper ras...   
1707   oral zinc therapy is indicated in zinc defici...   
1708     zidovudine, a nucleosidereverse transcripta...   
1709   zaleplon is indicated for the short-term trea...   
1710   zafirlukast is indicated for the prophylaxis ...   

                          therapeutic_class_description  \
0      disease-modifying antirheumatic drugs (dmards...   
1           hydrocortisone &amp; combined preparations    
2                       topical antiviral preparations    
3      herpes simplex &amp; varicella-zoster virus i...   
4                       ophthalmic anti-viral products    
...                                                 ...   
1706                         drugs used in diaper rash    
1707                     specific mineral preparations    
1708             drugs for hiv / anti-retroviral drugs    
1709   benzodiazepine hypnotics, benzodiazepine seda...   
1710                  leukotriene receptor antagonists    

                               pharmacology_description  \
0      adalimumab is a recombinant human igg1 monocl...   
1      acyclovir is a synthetic purine nucleoside an...   
2      acyclovir is an antiviral drug active against...   
3      aciclovir is a synthetic purine derivative. a...   
4      acyclovir is an antiviral agent which is high...   
...                                                 ...   
1706   zinc oxide is used to treat or prevent minor ...   
1707   zinc, a major mineral,plays a part in almost ...   
1708   zidovudine is converted intracellularly to zi...   
1709   zaleplon is a newer non-benzodiazepine hypnot...   
1710   zafirlukast is a selective and competitive le...   

                                     dosage_description  \
0       rheumatoid arthritis, psoriatic arthritis, a...   
1      the cream should be topically applied 5 times...   
2      acyclovircream should be applied five times p...   
3      treatment of in

In [11]:
import pandas as pd
from transformers import pipeline
from transformers import AutoTokenizer, AutoModelForTokenClassification

tokenizer = AutoTokenizer.from_pretrained("d4data/biomedical-ner-all")
model = AutoModelForTokenClassification.from_pretrained("d4data/biomedical-ner-all")

class DRUG_CLASS_CLASSIFICATION():

    def __init__(self):
        self.pipe = pipeline("ner", model=model, tokenizer=tokenizer, aggregation_strategy="simple", device=0) # pass device=0 if using gpu
        df = pd.read_csv('cleaned_generic_df_main.csv')
        drug_class_list = df['side_effects_description'].unique().tolist()
        # Remove nan values from the list
        drug_class_list = [item for item in drug_class_list if not pd.isna(item)]
        self.all_details = drug_class_list

    def classify_presciption_drugs(self):
        all_results = []
        all_details = self.all_details
        print(f'All Details: {all_details}')    
        # Pass the entire all_details list to the pipeline
        full_results = self.pipe(all_details)
        print(f'Results: {full_results}')
        for sentence_result, detail in zip(full_results, all_details):
            for result in sentence_result:
                if result is not None:
                    print(f'Result: {result}')
                    if len(str(result['word'])) >= 4 and '#' not in str(result['word']):
                        all_results.append({'Entity Group': result['entity_group'], 'Word': str(result['word']), 'Score': result['score'], 'Sentence': detail})
        # Return an empty DataFrame if no results are found
        if not all_results:
            return pd.DataFrame(columns=['Entity Group', 'Word', 'Score', 'Sentence'])
        return pd.DataFrame(all_results)

# Create an instance of the DRUG_CLASS_CLASSIFICATION class
drug_classifier = DRUG_CLASS_CLASSIFICATION()

# Classify the prescription drugs and save results in a pandas DataFrame
results_df = drug_classifier.classify_presciption_drugs()

# Print the DataFrame
print(results_df)


c:\Users\rifat\miniconda3\envs\tf\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


All Details: [' the most common adverse reaction with adalimumab was injection site reactions (erythema and/or itching, hemorrhage, pain or swelling). the most common adverse reactions leading to discontinuation of adalimumab in rheumatoid arthritis were clinical flare reaction, rash and pneumonia.  \r\n \r\n other adverse reactions of adalimumab includes- gastrointestinal disorders: diverticulitis, large bowel perforations including perforations associated with diverticulitis and appendiceal perforations associated with appendicitis, pancreatitis. \r\n general disorders and administration site conditions: pyrexia. \r\n hepato-biliary disorders: liver failure, hepatitis. \r\n immune system disorders: sarcoidosis. \r\n neoplasms benign, malignant and unspecified (including cysts and polyps): merkel cell carcinoma (neuroendocrine carcinoma of the skin). \r\n nervous system disorders: demyelinating disorders (e.g., optic neuritis, guillain-barr syndrome). \r\n cerebrovascular accident res

In [13]:
results_df.to_csv('side_effects.csv', index=False)

In [15]:
results_df['Score'] = pd.to_numeric(results_df['Score'], errors='coerce')

# Drop rows with score less than 0.7
results_df = results_df[results_df['Score'] >= 0.7]


In [17]:
results_df.to_csv('side_effects_.7_.csv', index=False)

In [54]:
results_df.to_csv('drug_class_results.csv', index=False)

In [46]:
import pandas as pd
from transformers import pipeline
from transformers import AutoTokenizer, AutoModelForTokenClassification

tokenizer = AutoTokenizer.from_pretrained("d4data/biomedical-ner-all")
model = AutoModelForTokenClassification.from_pretrained("d4data/biomedical-ner-all")

class DRUG_CLASS_CLASSIFICATION():

    def __init__(self):
        self.pipe = pipeline("ner", model=model, tokenizer=tokenizer, aggregation_strategy="simple", device=0) # pass device=0 if using gpu
        df = pd.read_csv('cleaned_generic_df_main.csv')
        drug_class_list = df['drug_class'].unique().tolist()
        self.all_details = drug_class_list

    def classify_presciption_drugs(self):
        all_results = []
        all_details = self.all_details
        print(f'All Details: {all_details}')    
        for detail in all_details:
            if detail is not None:
                print(f'Detail: {detail}')
                # Pass the detail as a list to the pipeline
                full_results = self.pipe([detail])
                print(f'Results: {full_results}')
                for results in full_results:
                    for result in results:
                        if result is not None:
                            print(f'Result: {result}')
                            if len(result['word']) >= 4 and '#' not in result['word']:
                                all_results.append({'Entity Group': result['entity_group'], 'Word': result['word'], 'Score': result['score'], 'Detail': detail})
        # Return an empty DataFrame if no results are found
        if not all_results:
            return pd.DataFrame(columns=['Entity Group', 'Word', 'Score', 'Detail'])
        return pd.DataFrame(all_results)

# Create an instance of the DRUG_CLASS_CLASSIFICATION class
drug_classifier = DRUG_CLASS_CLASSIFICATION()

# Classify the prescription drugs and save results in a pandas DataFrame
results_df = drug_classifier.classify_presciption_drugs()

# Print the DataFrame
print(results_df)


All Details: ['immunosuppressant', 'hydrocortisone & combined preparations', 'topical antiviral preparations', 'herpes simplex & varicella-zoster virus infections', 'ophthalmic anti-viral products', 'antidote preparations', 'combined bronchodilators', 'oral retinoid preparations', 'haemodialysis solutions', 'carbonic anhydrase inhibitor', 'non-steroidal anti-inflammatory drugs (nsaids)', 'drugs for osteoarthritis', 'herbal and nutraceuticals', 'drugs used in gout', nan, 'bph/ urinary retention/ urinary incontinence', 'vitamin in bone formation', 'combined preparations: inhibiting bone resorption', 'bisphosphonate preparations', 'protein kinase inhibitor', 'ophthalmic anti-allergic preparations', 'plasma expanders', 'anthelmintic', 'atypical anti-depressant drugs', 'cytotoxic chemotherapy', 'tyrosine kinase inhibitor', 'vaccines, anti-sera & immunoglobulin', 'other adrenoceptor stimulants', 'supplements & adjuvant therapy', 'drugs used in chronic kidney dialysis', 'parenteral nutritiona

c:\Users\rifat\miniconda3\envs\tf\lib\site-packages\transformers\pipelines\base.py:1081: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset
  warnings.warn(


ValueError: text input must of type `str` (single example), `List[str]` (batch or single pretokenized example) or `List[List[str]]` (batch of pretokenized examples).

In [39]:
all_results

NameError: name 'all_results' is not defined

In [36]:
import pandas as pd
from transformers import pipeline
from transformers import AutoTokenizer, AutoModelForTokenClassification

tokenizer = AutoTokenizer.from_pretrained("d4data/biomedical-ner-all")
model = AutoModelForTokenClassification.from_pretrained("d4data/biomedical-ner-all")

class DRUG_CLASS_CLASSIFICATION():

    def __init__(self):
        self.pipe = pipeline("ner", model=model, tokenizer=tokenizer, aggregation_strategy="simple",device=0) # pass device=0 if using gpu
        df = pd.read_csv('cleaned_generic_df_main.csv')
        drug_class_list = df['drug_class'].unique().tolist()
        self.all_details = drug_class_list

    def classify_presciption_drugs(self):
        all_results = []
        all_details = self.all_details
        print(f'All Details: {all_details}')    
        for detail in all_details:
            if detail is not None:
                print(f'Detail: {detail}')
                results = self.pipe(detail)
                for result in results:
                    if result is not None:
                        print(f'Result: {result}')
                        if len(result['word']) >= 4 and '#' not in result['word']:
                            all_results.append({'Entity Group': result['entity_group'], 'Word': result['word'], 'Score': result['score'], 'Detail': detail})
        return pd.DataFrame(all_results)  # Move this line outside the for loop


# Create an instance of the DRUG_CLASS_CLASSIFICATION class
drug_classifier = DRUG_CLASS_CLASSIFICATION()

# Classify the prescription drugs and save results in a pandas DataFrame
results_df = drug_classifier.classify_presciption_drugs()

# Print the DataFrame
print(results_df)


All Details: ['immunosuppressant', 'hydrocortisone & combined preparations', 'topical antiviral preparations', 'herpes simplex & varicella-zoster virus infections', 'ophthalmic anti-viral products', 'antidote preparations', 'combined bronchodilators', 'oral retinoid preparations', 'haemodialysis solutions', 'carbonic anhydrase inhibitor', 'non-steroidal anti-inflammatory drugs (nsaids)', 'drugs for osteoarthritis', 'herbal and nutraceuticals', 'drugs used in gout', nan, 'bph/ urinary retention/ urinary incontinence', 'vitamin in bone formation', 'combined preparations: inhibiting bone resorption', 'bisphosphonate preparations', 'protein kinase inhibitor', 'ophthalmic anti-allergic preparations', 'plasma expanders', 'anthelmintic', 'atypical anti-depressant drugs', 'cytotoxic chemotherapy', 'tyrosine kinase inhibitor', 'vaccines, anti-sera & immunoglobulin', 'other adrenoceptor stimulants', 'supplements & adjuvant therapy', 'drugs used in chronic kidney dialysis', 'parenteral nutritiona

c:\Users\rifat\miniconda3\envs\tf\lib\site-packages\transformers\pipelines\base.py:1081: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset
  warnings.warn(


ValueError: At least one input is required.

In [29]:
results_df

Empty DataFrame
Columns: []
Index: []

In [17]:
drug_class_classification = DRUG_CLASS_CLASSIFICATION()

In [18]:
drug_class=drug_class_classification.classify_presciption_drugs()

result: {'entity_group': 'Sign_symptom', 'score': 0.5923541, 'word': 'rash', 'start': 21, 'end': 25}


In [2]:
df

generic_name  \
0                     adalimumab   
1     acyclovir + hydrocortisone   
2            acyclovir (topical)   
3               acyclovir (oral)   
4         acyclovir (ophthalmic)   
...                          ...   
1706                  zinc oxide   
1707                zinc orotate   
1708                  zidovudine   
1709                    zaleplon   
1710                 zafirlukast   

                                             drug_class  \
0                                     immunosuppressant   
1                hydrocortisone & combined preparations   
2                        topical antiviral preparations   
3     herpes simplex & varicella-zoster virus infect...   
4                        ophthalmic anti-viral products   
...                                                 ...   
1706                          drugs used in diaper rash   
1707                      specific mineral preparations   
1708              drugs for hiv / anti-retroviral drugs   
1709                           benzodiazepine hypnotics   
1710                   leukotriene receptor antagonists   

                           indication  \
0                  ulcerative colitis   
1                     herpes labialis   
2                           sore lips   
3       varicella zoster (chickenpox)   
4             neonatal conjunctivitis   
...                               ...   
1706                   pressure sores   
1707                  severe diarrhea   
1708                    hiv infection   
1709  insomnia and sleep disturbances   
1710                   chronic asthma   

                                 indication_description  \
0        adalimumab is a tumor necrosis factor (tnf)...   
1      acyclovir &amp; hydrocortisone cream is indic...   
2      acyclovircream is a herpes simplex virus (hsv...   
3      aciclovir is indicated for- \r\n \r\n the tre...   
4      acyclovir is indicated for the treatment of h...   
...                                                 ...   
1706   zinc oxide helps treat and prevent diaper ras...   
1707   oral zinc therapy is indicated in zinc defici...   
1708     zidovudine, a nucleosidereverse transcripta...   
1709   zaleplon is indicated for the short-term trea...   
1710   zafirlukast is indicated for the prophylaxis ...   

                          therapeutic_class_description  \
0      disease-modifying antirheumatic drugs (dmards...   
1           hydrocortisone &amp; combined preparations    
2                       topical antiviral preparations    
3      herpes simplex &amp; varicella-zoster virus i...   
4                       ophthalmic anti-viral products    
...                                                 ...   
1706                         drugs used in diaper rash    
1707                     specific mineral preparations    
1708             drugs for hiv / anti-retroviral drugs    
1709   benzodiazepine hypnotics, benzodiazepine seda...   
1710                  leukotriene receptor antagonists    

                               pharmacology_description  \
0      adalimumab is a recombinant human igg1 monocl...   
1      acyclovir is a synthetic purine nucleoside an...   
2      acyclovir is an antiviral drug active against...   
3      aciclovir is a synthetic purine derivative. a...   
4      acyclovir is an antiviral agent which is high...   
...                                                 ...   
1706   zinc oxide is used to treat or prevent minor ...   
1707   zinc, a major mineral,plays a part in almost ...   
1708   zidovudine is converted intracellularly to zi...   
1709   zaleplon is a newer non-benzodiazepine hypnot...   
1710   zafirlukast is a selective and competitive le...   

                                     dosage_description  \
0       rheumatoid arthritis, psoriatic arthritis, a...   
1      the cream should be topically applied 5 times...   
2      acyclovircream should be applied five times p...   
3      treatment of in